 <h1 style="text-align: center; color: RED">BİRLİKTELİK KURALI TEMELLİ TAVSİYE SİSTEMİ</h1>

<span style="color: blue; font-weight: bold;">1-İŞ PROBLEMİ</span>

Sepet aşamasındaki kullanıcılara ürün önerisinde bulunmak.Problemimiz kişiler sepetlerine bir ürün eklediğinde hangi ürünleri önermeliyiz?


<span style="color: blue; font-weight: bold;">2-VERİ SETİ HİKAYESİ</span>

Online Retail II isimli veri seti İngiltere merkezli online bir satış mağazasının 01/12/2009-09/12/2011 tarihleri arasındaki satışlarını içermektedir. Bu şirketin ürün kataloğunda hediyelik eşyalar yer almaktadır.

**DEĞİŞKENLER**

InvoıceNo: Fatura Numarası
(Eğer bu kod C ile başlıyorsa işlemin iptal edildiğini ifade eder.)

StockCode:Ürün Kodu
(Her bir ürün için eşssiz numara)

Description:Ürün İsmi

Quantity: Ürün adedi(Faturalardaki ürünlerden kaçar tane satıldığını ifade etmektedir.)

InvoıceDate:Fatura Tarihi

UnitPrice:Fatura Fiyatı

CustomerID:eşsiz müşteri numarası

Country: Ülke ismi




<span style="color: blue; font-weight: bold;">3-VERİ ÖN İŞLEME</span>

In [12]:
!pip install mlxtend

In [1]:
import pandas as pd
from mlxtend.frequent_patterns import apriori, association_rules
'''
mlxtend (Machine Learning Extensions), Python'da makine öğrenmesi, veri bilimi ve veri madenciliği alanlarında kullanılan güçlü bir kütüphanedir. 
mlxtend.frequent_patterns modülü ise özellikle Birliktelik Kuralı Öğrenimi ve Sık Öğe Kümesi Madenciliği için oldukça popülerdir.
association_rules Fonksiyonu
Amacı: apriori veya başka bir sık öğe kümesi algoritmasından elde edilen kümeler üzerinden birliktelik kurallarını oluşturur.
Kullanımı: Verilen sık öğe kümelerine dayanarak support, confidence, lift gibi metrikler ile kuralları üretir.
Çıktı: Kuralların ve metriklerin bulunduğu bir DataFrame.
'''
pd.set_option('display.max_columns',None)
pd.set_option('display.width',500)
pd.set_option('display.expand_frame_repr',False)

In [3]:
df_= pd.read_excel("C:\\Users\\ASLI\\Desktop\\Data Scientist Bootcamp\\5. Recommendation Systems\\datasets\\online_retail_II.xlsx", sheet_name='Year 2010-2011')

In [5]:
df = df_.copy()

In [22]:
df.head()

Invoice StockCode                          Description  Quantity         InvoiceDate  Price  Customer ID         Country
0  536365    85123A   WHITE HANGING HEART T-LIGHT HOLDER         6 2010-12-01 08:26:00   2.55      17850.0  United Kingdom
1  536365     71053                  WHITE METAL LANTERN         6 2010-12-01 08:26:00   3.39      17850.0  United Kingdom
2  536365    84406B       CREAM CUPID HEARTS COAT HANGER         8 2010-12-01 08:26:00   2.75      17850.0  United Kingdom
3  536365    84029G  KNITTED UNION FLAG HOT WATER BOTTLE         6 2010-12-01 08:26:00   3.39      17850.0  United Kingdom
4  536365    84029E       RED WOOLLY HOTTIE WHITE HEART.         6 2010-12-01 08:26:00   3.39      17850.0  United Kingdom

In [7]:
df.describe().T

count                           mean                  min                  25%                  50%                  75%                  max          std
Quantity     541910.0                       9.552234             -80995.0                  1.0                  3.0                 10.0              80995.0   218.080957
InvoiceDate    541910  2011-07-04 13:35:22.342307584  2010-12-01 08:26:00  2011-03-28 11:34:00  2011-07-19 17:17:00  2011-10-19 11:27:00  2011-12-09 12:50:00          NaN
Price        541910.0                       4.611138            -11062.06                 1.25                 2.08                 4.13              38970.0    96.759765
Customer ID  406830.0                    15287.68416              12346.0              13953.0              15152.0              16791.0              18287.0  1713.603074

* Quantity ve Price eksi değer olamazken min kısmında eksi değerler olduğunu görüyoruz. Ayrıca %75 'lik değer ile max değeri karşılaştırdığımızda aykırı değer olduğunu gözlemliyoruz.

In [12]:
df.isnull().sum()#eksk değerler var

Invoice             0
StockCode           0
Description      1454
Quantity            0
InvoiceDate         0
Price               0
Customer ID    135080
Country             0
dtype: int64

In [16]:
df.shape

(541910, 8)

In [18]:
def retail_data_prep(dataframe):
    dataframe.dropna(inplace=True)#veri setindeki eksik değerleri siler.
    dataframe = dataframe[~dataframe['Invoice'].str.contains('C',na=False)]#iade olan faturalrı veri setinden cıkardık
    dataframe = dataframe[dataframe['Price'] > 0]#eksi değerlerden kurtulduk
    dataframe = dataframe[dataframe['Quantity']>0]#eksi değerlerden kurtulduk
    return dataframe
    

In [20]:
df = retail_data_prep(df)

In [22]:
df.describe().T

count                           mean                  min                  25%                  50%                  75%                  max          std
Quantity     397885.0                      12.988208                  1.0                  2.0                  6.0                 12.0              80995.0   179.331551
InvoiceDate    397885  2011-07-10 23:41:56.419316992  2010-12-01 08:26:00  2011-04-07 11:12:00  2011-07-31 14:39:00  2011-10-20 14:33:00  2011-12-09 12:50:00          NaN
Price        397885.0                       3.116525                0.001                 1.25                 1.95                 3.75              8142.75    22.097861
Customer ID  397885.0                   15294.416882              12346.0              13969.0              15159.0              16795.0              18287.0  1713.144421

In [30]:
#Aykırı değer: Bir  değişkendeki genel dağılımın dışında olan değerlere denir.
def outlier_thresholds(dataframe, variable, q1=0.01, q3=0.99):#aykırı değerler için eşik değerleri buluyoruz
    quartile1 = dataframe[variable].quantile(q1)
    quartile3 = dataframe[variable].quantile(q3)
    IQR = quartile3-quartile1
    up_limit= quartile3 + 1.5*IQR
    low_limit = quartile1 - 1.5*IQR
    return low_limit, up_limit
    

In [32]:
def replace_with_thresholds(dataframe, variable):#aykırı değerleri eşik değerlere baskılıyoruz
    low_limit, up_limit = outlier_thresholds(dataframe, variable)
    dataframe.loc[dataframe[variable] < low_limit, variable] = low_limit
    dataframe.loc[dataframe[variable] > up_limit, variable] = up_limit
    

In [34]:
replace_with_thresholds(df, 'Price')
replace_with_thresholds(df, 'Quantity')

C:\Users\ASLI\AppData\Local\Temp\ipykernel_21180\315995488.py:3: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '-177.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  dataframe.loc[dataframe[variable] < low_limit, variable] = low_limit


In [36]:
df.describe().T

count                           mean                  min                  25%                  50%                  75%                  max          std
Quantity     397885.0                       11.83077                  1.0                  2.0                  6.0                 12.0                298.5    25.523052
InvoiceDate    397885  2011-07-10 23:41:56.419316992  2010-12-01 08:26:00  2011-04-07 11:12:00  2011-07-31 14:39:00  2011-10-20 14:33:00  2011-12-09 12:50:00          NaN
Price        397885.0                       2.893492                0.001                 1.25                 1.95                 3.75                37.06     3.227175
Customer ID  397885.0                   15294.416882              12346.0              13969.0              15159.0              16795.0              18287.0  1713.144421

<span style="color: blue; font-weight: bold;">4-ARL VERİ YAPILARINI HAZIRLAMAK </span>

* Beklediğimiz yapı satırlarda Invoıce'lar, sütunlarda productlar, ve bir faturada ürünün olup olmamasının 1, 0 ile ifade edildiği matris şeklindeki yapı

In [42]:
df.head()

Invoice StockCode                          Description  Quantity         InvoiceDate  Price  Customer ID         Country
0  536365    85123A   WHITE HANGING HEART T-LIGHT HOLDER       6.0 2010-12-01 08:26:00   2.55      17850.0  United Kingdom
1  536365     71053                  WHITE METAL LANTERN       6.0 2010-12-01 08:26:00   3.39      17850.0  United Kingdom
2  536365    84406B       CREAM CUPID HEARTS COAT HANGER       8.0 2010-12-01 08:26:00   2.75      17850.0  United Kingdom
3  536365    84029G  KNITTED UNION FLAG HOT WATER BOTTLE       6.0 2010-12-01 08:26:00   3.39      17850.0  United Kingdom
4  536365    84029E       RED WOOLLY HOTTIE WHITE HEART.       6.0 2010-12-01 08:26:00   3.39      17850.0  United Kingdom

In [46]:
#Beklediğimiz yapıyı sadece bir ülkeye indirgeyerek yapacaz.
df_fr = df[df['Country']=='France']

In [48]:
#Fransa daki müşteriler için birliktelk kurallarını cıkarıcaz
df_fr.head()

Invoice StockCode                      Description  Quantity         InvoiceDate  Price  Customer ID Country
26  536370     22728        ALARM CLOCK BAKELIKE PINK      24.0 2010-12-01 08:45:00   3.75      12583.0  France
27  536370     22727        ALARM CLOCK BAKELIKE RED       24.0 2010-12-01 08:45:00   3.75      12583.0  France
28  536370     22726       ALARM CLOCK BAKELIKE GREEN      12.0 2010-12-01 08:45:00   3.75      12583.0  France
29  536370     21724  PANDA AND BUNNIES STICKER SHEET      12.0 2010-12-01 08:45:00   0.85      12583.0  France
30  536370     21883                 STARS GIFT TAPE       24.0 2010-12-01 08:45:00   0.65      12583.0  France

In [56]:
df_fr.groupby(['Invoice','Description']).agg({'Quantity':'sum'})#hangi faturada hangi üründen kaçar tane var bilgisini verir.

Quantity
Invoice Description                               
536370   SET 2 TEA TOWELS I LOVE LONDON       24.0
        ALARM CLOCK BAKELIKE GREEN            12.0
        ALARM CLOCK BAKELIKE PINK             24.0
        ALARM CLOCK BAKELIKE RED              24.0
        CHARLOTTE BAG DOLLY GIRL DESIGN       20.0
...                                            ...
581587  PACK OF 20 SPACEBOY NAPKINS           12.0
        PLASTERS IN TIN CIRCUS PARADE         12.0
        PLASTERS IN TIN STRONGMAN             12.0
        POSTAGE                                1.0
        SPACEBOY LUNCH BOX                    12.0

[8306 rows x 1 columns]

In [60]:
#Bizim istediğimiz yapı faturların tek olması ve sutunlarda description olması
df_fr.pivot_table(index = 'Invoice', columns = 'Description', values = 'Quantity', aggfunc='sum', fill_value=0 )#fill_value nan yerine sıfır yazar

Description   50'S CHRISTMAS GIFT BAG LARGE   DOLLY GIRL BEAKER   I LOVE LONDON MINI BACKPACK   NINE DRAWER OFFICE TIDY   SET 2 TEA TOWELS I LOVE LONDON    SPACEBOY BABY GIFT SET   TRELLIS COAT RACK  10 COLOUR SPACEBOY PEN  12 COLOURED PARTY BALLOONS  12 EGG HOUSE PAINTED WOOD  12 MESSAGE CARDS WITH ENVELOPES  12 PENCIL SMALL TUBE WOODLAND  12 PENCILS SMALL TUBE RED RETROSPOT  12 PENCILS SMALL TUBE SKULL  12 PENCILS TALL TUBE POSY  12 PENCILS TALL TUBE RED RETROSPOT  12 PENCILS TALL TUBE WOODLAND  15CM CHRISTMAS GLASS BALL 20 LIGHTS  16 PIECE CUTLERY SET PANTRY DESIGN  18PC WOODEN CUTLERY SET DISPOSABLE  20 DOLLY PEGS RETROSPOT  200 RED + WHITE BENDY STRAWS  3 HOOK HANGER MAGIC GARDEN  3 PIECE SPACEBOY COOKIE CUTTER SET  3 RAFFIA RIBBONS 50'S CHRISTMAS   3 STRIPEY MICE FELTCRAFT  3 TIER CAKE TIN RED AND CREAM  3 TRADITIONAl BISCUIT CUTTERS  SET  36 DOILIES DOLLY GIRL  36 DOILIES VINTAGE CHRISTMAS  36 FOIL HEART CAKE CASES  36 FOIL STAR CAKE CASES   36 PENCILS TUBE RED RETROSPOT  36 PENCILS TUBE SKULLS  36 PENCILS TUBE WOODLAND  3D HEARTS  HONEYCOMB PAPER GARLAND  3D TRADITIONAL CHRISTMAS STICKERS  3D VINTAGE CHRISTMAS STICKERS   4 IVORY DINNER CANDLES SILVER FLOCK  4 PINK DINNER CANDLE SILVER FLOCK  4 TRADITIONAL SPINNING TOPS  5 HOOK HANGER MAGIC TOADSTOOL  5 HOOK HANGER RED MAGIC TOADSTOOL  6 GIFT TAGS 50'S CHRISTMAS   6 GIFT TAGS VINTAGE CHRISTMAS   6 RIBBONS EMPIRE    6 RIBBONS RUSTIC CHARM  6 ROCKET BALLOONS   60 CAKE CASES DOLLY GIRL DESIGN  60 CAKE CASES VINTAGE CHRISTMAS  60 TEATIME FAIRY CAKE CASES  6PC WOOD PLATE SET DISPOSABLE  72 SWEETHEART FAIRY CAKE CASES  A PRETTY THANK YOU CARD  ABC TREASURE BOOK BOX   ADULT APRON APPLE DELIGHT  ADVENT CALENDAR GINGHAM SACK  AGED GLASS SILVER T-LIGHT HOLDER  AIRLINE BAG VINTAGE JET SET BROWN  AIRLINE BAG VINTAGE JET SET RED  AIRLINE BAG VINTAGE JET SET WHITE  AIRLINE BAG VINTAGE TOKYO 78  AIRLINE BAG VINTAGE WORLD CHAMPION   AIRLINE LOUNGE,METAL SIGN  ALARM CLOCK BAKELIKE CHOCOLATE  ALARM CLOCK BAKELIKE GREEN  ALARM CLOCK BAKELIKE IVORY  ALARM CLOCK BAKELIKE ORANGE  ALARM CLOCK BAKELIKE PINK  ALARM CLOCK BAKELIKE RED   ALPHABET HEARTS STICKER SHEET  ALUMINIUM STAMPED HEART  AMETHYST CHUNKY BEAD BRACELET W STR  ANGEL DECORATION STARS ON DRESS  ANTIQUE ALL GLASS CANDLESTICK  ANTIQUE GLASS DRESSING TABLE POT  ANTIQUE GLASS PEDESTAL BOWL  ANTIQUE SILVER BAUBLE LAMP    ANTIQUE SILVER T-LIGHT GLASS  ANTIQUE SILVER TEA GLASS ENGRAVED  APPLE BATH SPONGE  AREA PATROLLED METAL SIGN  ASS COLOUR GLOWING TIARAS  ASS FLORAL PRINT MULTI SCREWDRIVER  ASSORTED BOTTLE TOP  MAGNETS   ASSORTED COLOUR BIRD ORNAMENT  ASSORTED COLOUR MINI CASES  ASSORTED COLOUR T-LIGHT HOLDER  ASSORTED COLOURS SILK FAN  ASSORTED EASTER DECORATIONS  BELLS  ASSORTED EASTER GIFT TAGS  ASSORTED FLOWER COLOUR "LEIS"  ASSORTED TUTTI FRUTTI BRACELET  ASSORTED TUTTI FRUTTI MIRROR  ASSORTED TUTTI FRUTTI SMALL PURSE  ASSTD DESIGN 3D PAPER STICKERS  ASSTD DESIGN RACING CAR PEN  ASSTD FRUIT+FLOWERS FRIDGE MAGNETS  ASSTD RASTA KEY-CHAINS  BABUSHKA LIGHTS STRING OF 10  BAG 125g SWIRLY MARBLES  BAG 250g SWIRLY MARBLES  BAKING MOULD CHOCOLATE CUPCAKES  BAKING MOULD EASTER EGG MILK CHOC  BAKING MOULD EASTER EGG WHITE CHOC  BAKING MOULD HEART MILK CHOCOLATE  BAKING MOULD HEART WHITE CHOCOLATE  BAKING SET 9 PIECE RETROSPOT   BAKING SET SPACEBOY DESIGN  BALLOON ART MAKE YOUR OWN FLOWERS  BALLOON PUMP WITH 10 BALLOONS  BALLOON WATER BOMB PACK OF 35  BALLOONS  WRITING SET   BANQUET BIRTHDAY  CARD    BASKET OF TOADSTOOLS  BATH BUILDING BLOCK WORD  BEADED CRYSTAL HEART BLUE  LARGE  BELLE JARDINIERE CUSHION COVER  BEWARE OF THE CAT METAL SIGN   BIG DOUGHNUT FRIDGE MAGNETS  BILI NUT AND WOOD NECKLACE  BINGO SET  BIRD DECORATION GREEN POLKADOT  BIRD DECORATION RED RETROSPOT  BIRD HOUSE HOT WATER BOTTLE  BIRDS MOBILE VINTAGE DESIGN  BIRTHDAY CARD, RETRO SPOT  BISCUIT TIN 50'S CHRISTMAS  BISCUIT TIN VINTAGE CHRISTMAS  BISCUIT TIN VINTAGE GREEN  BISCUIT TIN VINTAGE RED  BLACK AND WHITE CAT BOWL  BLACK CANDELABRA T-LIGHT HOLDER  BLACK CHRISTMAS TR

In [62]:
#yuakrıdaki yapıyı unstack metodu ile de yapabiliriz.
df_fr.groupby(['Invoice','Description']).agg({'Quantity':'sum'}).unstack()

Quantity                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        

**NOT**:Veri analitiğinde unstack(), verideki dikey yapıyı yataya çevirmek için kullanılır. Pivot gibi davranır ama biraz daha esnek ve zincirleme işlemlerde kullanışlıdır.unstack() → Satırlardaki bir seviyeyi sütunlara taşır.
Yani:
index (satır) ➡️ columns (sütun) haline gelir.

In [65]:
#Nan değerleri 0 dolu değerleri 1 olarak göstermeliyiz.
df_fr.groupby(['Invoice','Description']).agg({'Quantity':'sum'}).unstack().fillna(0)

Quantity                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        

In [68]:
df_fr.groupby(['Invoice','Description']).\
      agg({'Quantity':'sum'}). \
      unstack(). \
      fillna(0). \
      applymap(lambda x : 1 if x > 0 else 0)

C:\Users\ASLI\AppData\Local\Temp\ipykernel_21180\894767014.py:5: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  applymap(lambda x : 1 if x > 0 else 0)


Quantity                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        

**NOT**:applymap fonksiyonu  sadece DataFrame nesnesinde kullanılabilir ve doğrudan tek tek her bir hücreye (bireysel değere) uygulanır. Yani satır veya sütun değil, doğrudan tüm hücreleri tek tek ele alır. Genellikle tüm veriye aynı işlemin uygulanması gerektiğinde kullanılır. Özellikle sayısal verileri dönüştürmek (örneğin: her değeri 1 ile karşılaştırıp 0 veya 1 yapmak, her değerin karesini almak) veya string veriler üzerinde işlem yapmak (örneğin: her hücredeki metni küçük harfe çevirmek) için uygundur.

apply() satır veya sütun düzeyinde işlem yaparken, applymap() hücre düzeyinde işlem yapar. Series nesnesinde yalnızca apply() kullanılabilir, applymap() ise sadece DataFrame için geçerlidir.



In [70]:
#Ürünlerin iismlerine göre değilde code'larına göre oluşturmak istersek
def create_invoice_product_df(dataframe, id=False):
    if id:
        return df_fr.groupby(['Invoice','StockCode']).\
               agg({'Quantity':'sum'}). \
               unstack(). \
               fillna(0). \
               applymap(lambda x : 1 if x > 0 else 0)
    else:
        return df_fr.groupby(['Invoice','Description']).\
               agg({'Quantity':'sum'}). \
               unstack(). \
               fillna(0). \
               applymap(lambda x : 1 if x > 0 else 0)
        

In [106]:
fr_inv_pro_df = create_invoice_product_df(df_fr, id=True)

C:\Users\ASLI\AppData\Local\Temp\ipykernel_21180\4080477289.py:8: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  applymap(lambda x : 1 if x > 0 else 0)


In [114]:
fr_inv_pro_df.head()

Quantity                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        

In [118]:
print(fr_inv_pro_df.columns)#multiindex yapısı var

MultiIndex([('Quantity',    10002),
            ('Quantity',    10120),
            ('Quantity',    10125),
            ('Quantity',    10135),
            ('Quantity',    11001),
            ('Quantity',    15036),
            ('Quantity',    15039),
            ('Quantity',    16012),
            ('Quantity',    16048),
            ('Quantity',    16218),
            ...
            ('Quantity', '85232D'),
            ('Quantity', '90030B'),
            ('Quantity', '90030C'),
            ('Quantity', '90184B'),
            ('Quantity', '90184C'),
            ('Quantity', '90201B'),
            ('Quantity', '90201C'),
            ('Quantity',     'C2'),
            ('Quantity',      'M'),
            ('Quantity',   'POST')],
           names=[None, 'StockCode'], length=1522)


In [120]:
fr_inv_pro_df.columns = fr_inv_pro_df.columns.get_level_values(1)#coklu index yapısından kurtulduk.

In [122]:
print(fr_inv_pro_df.columns)

Index([   10002,    10120,    10125,    10135,    11001,    15036,    15039,    16012,    16048,    16218,
       ...
       '85232D', '90030B', '90030C', '90184B', '90184C', '90201B', '90201C',     'C2',      'M',   'POST'], dtype='object', name='StockCode', length=1522)


In [84]:
#Hangi stokcode hangi ürüne ait görmek istersem
def check_id(dataframe, stockcode):
    product_name = dataframe[dataframe['StockCode']==stockcode][['Description']].values[0].tolist()
    print(product_name)

In [86]:
check_id(df_fr, 10002)

['INFLATABLE POLITICAL GLOBE ']


* 1. dataframe['StockCode'] == stockcode
     Bu, StockCode sütununda, stockcode değişkenine eşit olan satırları bulur.Çıktısı bir Boolean Series olur.
     
  2. dataframe[dataframe['StockCode'] == stockcode]
     Bu, yukarıdaki Boolean serisini kullanarak sadece eşleşen satırları getirir.
 
  3. [['Description']]
     Filtrelenen satırların sadece Description sütununu almak istiyoruz.Çift köşeli parantez, DataFrame formatını korur (tek köşeli olsaydı Series dönerdi).
 
     
  4. .values
     Bu ifade DataFrame’i NumPy array’ine çevirir.Çıktı:array([['RED WOOLLY HOTTIE']], dtype=object)

  5. [0]
     Bu, ilk satırı seçer. (yani: ['RED WOOLLY HOTTIE'])
 
   6. .tolist()
     Bu NumPy array'ini Python listesine çevirir.
  

In [88]:
#alternatif yöntem
def check_id(dataframe, stockcode):
    product_name = dataframe.loc[dataframe['StockCode'] == stockcode, 'Description'].values[0]
    print(product_name)

In [94]:
check_id(df_fr, 10120)

DOGGY RUBBER


<span style="color: blue; font-weight: bold;">5-BİRLİKTELİK KURALLARININ ÇIKARILMASI </span>

İlk olarak amacımız apriori fonksiyonu ile olası tüm ürün birlikteliklerinin support değerlerini yani olasılıklarını bulmak olacaktır. 

In [124]:
frequent_itemsets = apriori(fr_inv_pro_df,
                           min_support=0.01,
                           use_colnames=True)

C:\Users\ASLI\anaconda3\Lib\site-packages\mlxtend\frequent_patterns\fpcommon.py:161: DeprecationWarning: DataFrames with non-bool types result in worse computationalperformance and their support might be discontinued in the future.Please use a DataFrame with bool type
  warnings.warn(


In [126]:
frequent_itemsets.sort_values('support', ascending=False)#her bir ürünün olasılıkları

support                                           itemsets
538    0.773779                                             (POST)
387    0.187661                                            (23084)
107    0.179949                                            (21731)
243    0.172237                                            (22554)
245    0.169666                                            (22556)
...         ...                                                ...
18793  0.010283                       (22729, 21086, 22326, 22551)
18787  0.010283                       (23256, 21086, 22492, 22326)
18786  0.010283                       (22728, 21086, 22492, 22326)
18785  0.010283                       (21086, 22492, 22326, 22727)
40654  0.010283  (22659, 23206, 22726, 22727, 22728, 20750, 223...

[40655 rows x 2 columns]

In [128]:
#Birliktelik kurallarının çıkarılması
rules = association_rules(frequent_itemsets,
                          metric = 'support',
                          min_threshold=0.01)

* association_rules, sık kullanılan ürün kümeleri (frequent itemsets) üzerinde çalışarak,birliktelik kuralları (if-then şeklinde) çıkarır.Örneğin, “Eğer müşteri A ürününü almışsa, B ürününü de alma ihtimali nedir?” gibi kurallar üretir.

* metric='support'

Hangi kriter baz alınarak kurallar oluşturulacak?support, confidence, lift, leverage gibi farklı metrikler olabilir.Burada support (destek) kriteri seçilmiş, yani kuralların destek değeri belirlenen eşik üzerinde olmalı

* min_threshold=0.01 Seçilen metrik için minimum eşik değer.


In [131]:
rules

antecedents                                        consequents  antecedent support  consequent support   support  confidence       lift  representativity  leverage  conviction  zhangs_metric   jaccard  certainty  kulczynski
0           (10002)                                            (21791)            0.020566            0.028278  0.010283    0.500000  17.681818               1.0  0.009701    1.943445       0.963255  0.266667   0.485450    0.431818
1           (21791)                                            (10002)            0.028278            0.020566  0.010283    0.363636  17.681818               1.0  0.009701    1.539111       0.970899  0.266667   0.350274    0.431818
2           (10002)                                            (21915)            0.020566            0.069409  0.010283    0.500000   7.203704               1.0  0.008855    1.861183       0.879265  0.129032   0.462707    0.324074
3           (21915)                                            (10002)            0.069409            0.020566  0.010283    0.148148   7.203704               1.0  0.008855    1.149771       0.925414  0.129032   0.130261    0.324074
4           (10002)                                            (22551)            0.020566            0.136247  0.010283    0.500000   3.669811               1.0  0.007481    1.727506       0.742782  0.070175   0.421131    0.287736
...             ...                                                ...                 ...                 ...       ...         ...        ...               ...       ...         ...            ...       ...        ...         ...
1372699     (23254)  (22659, 23206, 22726, 22727, 22728, 20750, 223...            0.071979            0.010283  0.010283    0.142857  13.892857               1.0  0.009543    1.154670       1.000000  0.142857   0.133952    0.571429
1372700     (22326)  (22659, 23206, 22726, 22727, 22728, 20750, 223...            0.159383            0.010283  0.010283    0.064516   6.274194               1.0  0.008644    1.057974       1.000000  0.064516   0.054797    0.532258
1372701     (21558)  (22659, 23206, 22726, 22727, 22728, 20750, 223...            0.051414            0.010283  0.010283    0.200000  19.450000               1.0  0.009754    1.237147       1.000000  0.200000   0.191688    0.600000
1372702     (23291)  (22659, 23206, 22726, 22727, 22728, 20750, 223...            0.041131            0.010283  0.010283    0.250000  24.312500               1.0  0.009860    1.319623       1.000000  0.250000   0.242208    0.625000
1372703     (23199)  (22659, 23206, 22726, 22727, 22728, 20750, 223...            0.066838            0.010283  0.010283    0.153846  14.961538               1.0  0.009595    1.169666       1.000000  0.153846   0.145055    0.576923

[1372704 rows x 14 columns]

* association_rules fonksiyonu, sık ürün kümelerinden (frequent itemsets)

* Tüm mümkün olan kural kombinasyonlarını (antecedent → consequent) çıkarır.

* Örneğin, {A, B} → {C} gibi, “A ve B alınmışsa C alınma ihtimali nedir?”

* Sonra seçilen metrik (burada support) bazında filtre uygular.

* Burada:

antecedents: "If" kısmı (ön koşul ürünler) yani 1. ürün

consequents: "Then" kısmı (sonuç ürünler) yani 2. ürün

antecedent support:1. ürünün tek başına gözlemlenme olasılığı

consequent support:2. ürünün tek başına gözlemlenme olasılığı


support: kuraldaki tüm ürünlerin birlikte görülme oranı

confidence: kuralın doğruluk oranı (antecedents alındığında consequents alma olasılığı)

lift: kuralın güçlülüğü, 1’den büyükse anlamlı(X ürünü satın alındığında y ürünün satın alma olasılığı lift kat kadar artar)

conviction: Y ürünü olmadan X ürünün beklenen frekansıdır.



In [134]:
rules[(rules["support"]>0.05) & (rules["confidence"]>0.1) & (rules["lift"]>5)]. \
sort_values("confidence", ascending=False)

antecedents    consequents  antecedent support  consequent support   support  confidence      lift  representativity  leverage  conviction  zhangs_metric   jaccard  certainty  kulczynski
23707         (21080, 21094)        (21086)            0.102828            0.138817  0.100257    0.975000  7.023611               1.0  0.085983   34.447301       0.955918  0.709091   0.970970    0.848611
23706         (21080, 21086)        (21094)            0.102828            0.128535  0.100257    0.975000  7.585500               1.0  0.087040   34.858612       0.967673  0.764706   0.971313    0.877500
108820  (21080, POST, 21086)        (21094)            0.084833            0.128535  0.082262    0.969697  7.544242               1.0  0.071358   28.758355       0.947858  0.627451   0.965227    0.804848
108821  (21080, POST, 21094)        (21086)            0.084833            0.138817  0.082262    0.969697  6.985410               1.0  0.070486   28.419023       0.936271  0.581818   0.964812    0.781145
1777                 (21094)        (21086)            0.128535            0.138817  0.123393    0.960000  6.915556               1.0  0.105550   21.529563       0.981563  0.857143   0.953552    0.924444
...                      ...            ...                 ...                 ...       ...         ...       ...               ...       ...         ...            ...       ...        ...         ...
7212                 (22629)        (22630)            0.125964            0.100257  0.071979    0.571429  5.699634               1.0  0.059351    2.099400       0.943382  0.466667   0.523673    0.644689
62249                (22630)  (POST, 22629)            0.100257            0.100257  0.053985    0.538462  5.370809               1.0  0.043933    1.949443       0.904490  0.368421   0.487033    0.538462
62244          (POST, 22629)        (22630)            0.100257            0.100257  0.053985    0.538462  5.370809               1.0  0.043933    1.949443       0.904490  0.368421   0.487033    0.538462
62248                (22629)  (POST, 22630)            0.125964            0.074550  0.053985    0.428571  5.748768               1.0  0.044594    1.619537       0.945098  0.368421   0.382540    0.576355
5519                 (22382)        (22662)            0.120823            0.084833  0.051414    0.425532  5.016119               1.0  0.041164    1.593069       0.910673  0.333333   0.372281    0.515796

[84 rows x 14 columns]

<span style="color: blue; font-weight: bold;">6-ÇALIŞMANIN SCRİPTİNİ HAZIRLAMA </span>

In [145]:
def outlier_thresholds(dataframe, variable):
    quartile1 = dataframe[variable].quantile(0.01)
    quartile3 = dataframe[variable].quantile(0.99)
    interquantile_range = quartile3 - quartile1
    up_limit = quartile3 + 1.5 * interquantile_range
    low_limit = quartile1 - 1.5 * interquantile_range
    return low_limit, up_limit

def replace_with_thresholds(dataframe, variable):
    low_limit, up_limit = outlier_thresholds(dataframe, variable)
    dataframe.loc[(dataframe[variable] < low_limit), variable] = low_limit
    dataframe.loc[(dataframe[variable] > up_limit), variable] = up_limit

def retail_data_prep(dataframe):
    dataframe.dropna(inplace=True)
    dataframe = dataframe[~dataframe["Invoice"].str.contains("C", na=False)]
    dataframe = dataframe[dataframe["Quantity"] > 0]
    dataframe = dataframe[dataframe["Price"] > 0]
    replace_with_thresholds(dataframe, "Quantity")
    replace_with_thresholds(dataframe, "Price")
    return dataframe


def create_invoice_product_df(dataframe, id=False):
    if id:
        return dataframe.groupby(['Invoice', "StockCode"])['Quantity'].sum().unstack().fillna(0). \
            applymap(lambda x: 1 if x > 0 else 0)
    else:
        return dataframe.groupby(['Invoice', 'Description'])['Quantity'].sum().unstack().fillna(0). \
            applymap(lambda x: 1 if x > 0 else 0)


def check_id(dataframe, stock_code):
    product_name = dataframe[dataframe["StockCode"] == stock_code][["Description"]].values[0].tolist()
    print(product_name)


def create_rules(dataframe, id=True, country="France"):
    dataframe = dataframe[dataframe['Country'] == country]
    dataframe = create_invoice_product_df(dataframe, id)
    frequent_itemsets = apriori(dataframe, min_support=0.01, use_colnames=True)
    rules = association_rules(frequent_itemsets, metric="support", min_threshold=0.01)
    return rules


<span style="color: blue; font-weight: bold;">7-ÜRÜN ÖNERME UYGULAMASI </span>

In [147]:
# Örnek:
# Kullanıcı örnek ürün id: 22492
product_id = 22492
check_id(df, product_id)

['MINI PAINT SET VINTAGE ']


In [149]:
sorted_rules = sorted_rules = rules.sort_values("lift", ascending=False)#bizim için lift öenmliydi ona göre sıraldık istersek başka metriğe görede sıralama yapabiliriz.

In [153]:
sorted_rules.head()

antecedents                   consequents  antecedent support  consequent support   support  confidence   lift  representativity  leverage  conviction  zhangs_metric  jaccard  certainty  kulczynski
1082358         (22659, 23206, 22726, 22727)  (21558, 23254, 22326, 23199)            0.010283            0.010283  0.010283         1.0  97.25               1.0  0.010177         inf            1.0      1.0        1.0         1.0
1160023  (22727, 22728, 22352, 23254, 23199)  (22326, 21558, 22726, 20750)            0.010283            0.010283  0.010283         1.0  97.25               1.0  0.010177         inf            1.0      1.0        1.0         1.0
1160025  (22727, 22728, 21558, 23254, 22326)  (22352, 23199, 22726, 20750)            0.010283            0.010283  0.010283         1.0  97.25               1.0  0.010177         inf            1.0      1.0        1.0         1.0
1160026  (22727, 22728, 23254, 22326, 23199)  (22352, 21558, 22726, 20750)            0.010283            0.010283  0.010283         1.0  97.25               1.0  0.010177         inf            1.0      1.0        1.0         1.0
1160027  (22727, 22728, 21558, 22326, 23199)  (22352, 23254, 22726, 20750)            0.010283            0.010283  0.010283         1.0  97.25               1.0  0.010177         inf            1.0      1.0        1.0         1.0

In [155]:
#kod bloğu, bir ürün için önerilecek diğer ürünleri bulma mantığını temsil ediyor ve association rules çıktılarını kullanıyor. 

recommendation_list = []#önerilecek ürünlerin iismlerinin ekleneceği boş bir liste oluşturduk
for i, product in enumerate(sorted_rules["antecedents"]):
    for j in list(product):
        if j == product_id:
            recommendation_list.append(list(sorted_rules.iloc[i]["consequents"])[0])

recommendation_list[0:3]

[22556, 22551, 22326]

1️⃣ recommendation_list = []

Boş bir liste oluşturuyoruz.
Buraya önerilecek ürünlerin isimleri eklenecek.

2️⃣ for i, product in enumerate(sorted_rules["antecedents"]):

sorted_rules isimli DataFrame'deki "antecedents" sütununu tek tek dolaşıyoruz.
enumerate() ile hem indeksi (i), hem de değerini (product) alıyoruz.
antecedents: Kuralların "if" yani ön koşul ürünleri seti. Örneğin {A}, {B, C} gibi.

3️⃣ for j in list(product):

product aslında bir frozenset (değiştirilemez set) olarak geliyor.
Bu set içindeki her ürünü (j) tek tek dolaşmak için listeye çevriliyor.

4️⃣ if j == product_id:

Eğer ön koşuldaki ürünlerden (j) biri, aradığımız product_id (yani kullanıcı sorguladığı ürün) ile eşleşirse, o kuralın sonuç kısmını alacağız.

5️⃣ recommendation_list.append(list(sorted_rules.iloc[i]["consequents"])[0])

O anki kuralın (i indeksli satırın) "consequents" sütunundaki ürün seti alınır.
Bu set yine frozenset olduğu için listeye çevrilir.
Liste içinden ilk ürün seçilir (genellikle tek ürün olur).
Bu ürün, öneriler listesine (recommendation_list) eklenir.

In [157]:
def arl_recommender(rules_df, product_id, rec_count=1):
    sorted_rules = rules_df.sort_values("lift", ascending=False)
    recommendation_list = []
    for i, product in enumerate(sorted_rules["antecedents"]):
        for j in list(product):
            if j == product_id:
                recommendation_list.append(list(sorted_rules.iloc[i]["consequents"])[0])

    return recommendation_list[0:rec_count]


In [161]:
arl_recommender(rules, 22492, 1)#1 ürün önerir
arl_recommender(rules, 22492, 2)#2 ürün önerir
arl_recommender(rules, 22492, 3)#3 ürün önerir

[22556, 22551, 22326]